# $$
\text{Résolution de systèmes non linéaires}
$$

### Objectifs :

- implémenter les méthodes de Picard, de Newton-Raphson, de la sécante, et de la dichotomie ;
- estimer la vitesse de convergence de ces différentes méthodes.

## I. Méthode du point fixe de Banach-Picard

Nous cherchons à résoudre un système non linéaire écrit sous la forme
$$
F(x) = x,
$$
où $F$ est une application définie sur un sous-ensemble fermé $X$ de $\mathbb{R}^m$, à valeurs dans $\mathbb R^m$. Si $F$ est une contraction sur ce sous-ensemble, alors le théorème du point fixe de Banach-Picard assure qu'elle y admet un unique point fixe $x^*$, qui est donc solution de l'équation considérée. Étant donné un point $x_0 \in X$, nous savons de plus que
$$
\lim_{n \to + \infty} F^n(x_0) =x^*.
$$
L'algorithme du point fixe consiste donc à choisir un point $x_0$ arbitrairement, puis à calculer $x_1 = F(x_0)$, $x_2 = F(x_1)$, et ainsi de suite.

Notons que dans le cas où $x_0$ n'appartient pas à l'ensemble fermé $X$ sur lequel $F$ est une contraction, l'algorithme peut ne pas converger. Étant donnés un seuil d'erreur $\varepsilon > 0$ et un nombre maximal d'itérations $N \geq 0$, nous décidons d'arrêter l'algorithme soit lorsque 
$$
|F(x_n) - x_n| < \varepsilon,
$$
auquel cas il retourne la valeur approchée $x_n$ du point fixe, soit lorsque le nombre d'itérations a dépassé $N$, auquel cas il renvoie le message "L'algorithme n'a pas convergé" :

In [1]:
import numpy as np
def Banach(f,x0,eps,N):
    e=2*eps
    x=x0
    n=0
    while n<N and e>eps:
        x=f(x)
        n=n+1
        e=np.linalg.norm(x-f(x))
    if n<N:
        return(x)
    else:
        return("L'algorithme n'a pas convergé.")
# Test de la fonction Banach pour la fonction f(x,y) = (arctan(y),cos(x)/2)
def F1(x):
    return(np.array([np.arctan(x[1]),np.cos(x[0])/2]))
x=Banach(F1,np.array([0,0]),0.00001,50)
print('x =',x,'\n')
print(F1(x)-x)

x = [0.42707295 0.45508306] 

[0.00000000e+00 7.96707067e-06]


La routine `scipy.optimize.fixed_point(f,x0)` calcule numériquement la solution du problème de point fixe $x = f(x)$ en débutant à $x_0$. Elle implémente une méthode plus robuste que celle du point fixe que nous ne détaillerons pas :

In [2]:
import scipy.optimize as sc_opt 
print('x =',sc_opt.fixed_point(F1,np.array([0,0])),'\n')

x = [0.42707859 0.45508986] 



## II. Méthode de Newton-Raphson

Nous cherchons désormais à résoudre l'équation
$$
F(x) = 0,
$$
dans laquelle $F$ est une fonction différentiable sur $\mathbb{R}^m$. Étant donné un point $x_0 \in \mathbb{R}^m$, nous pouvons approcher $F$ par la fonction affine qui correspond à sa linéarisation en $x_0$
$$
F_\text{app}(x) = F(x_0) + J F(x_0) \big( x - x_0 \big),
$$
où $J F$ est la matrice Jacobienne de $F$. La fonction $F_\text{app}$ s'annule au point
$$
x_1 = x_0 + h,
$$
où $h$ est solution de l'équation
$$
JF(x_0) h = - F(x_0).
$$
Lorsque la matrice $J F(x_0)$ est inversible, le vecteur $h$ est égal à $- JF(x_0)^{- 1} F(x_0)$. En pratique, il est plus efficace de le déterminer à l'aide d'une méthode de résolution des systèmes linéaires, par exemple la méthode du pivot de Gauss.

Nous pouvons alors itérer cette opération pour déterminer un point $x_1$, puis un point $x_2$, et ainsi de suite. La suite $(x_n)_{n \geq 0}$ ainsi définie peut ne pas converger, par exemple si le point d'initialisation $x_0$ est trop loin du vrai zéro $x^*$ de la fonction $F$. Étant donnés un seuil $\varepsilon > 0$ et un nombre maximum d'itérations $N \geq 1$, nous arrêtons donc l'algorithme soit lorsque $|F(x_n)| < \varepsilon$ et il renvoie alors la valeur de $x_n$, soit lorsque le nombre d'itérations dépasse $N$ auquel cas il renvoie le message "L'algorithme n'a pas convergé" :

In [3]:
import numpy as np
def Newton_Raphson(F,JF,x0,eps,N):
    e=2*eps
    n=0
    x=x0
    while e>eps and n<N:
        x=x-np.linalg.solve(JF(x),F(x))
        e=np.linalg.norm(F(x))
        n=n+1
    if n<N:
        return(x)
    else:
        return("L'algorithme n'a pas convergé.")
# Test de la fonction Newton_Raphson pour déterminer la solution (x,y) des équations cos(x)-sin(y)=exp(−x)-cos(y)=0
def F2(x):
    return(np.array([np.cos(x[0])-np.sin(x[1]),np.exp(-x[0])-np.cos(x[1])]))
def JF2(x):
    A=np.zeros([2,2])
    A[0,0]=-np.sin(x[0])
    A[1,0]=-np.exp(x[0])
    A[0,1]=-np.cos(x[1])
    A[1,1]=np.sin(x[1])
    return(A)
x2=Newton_Raphson(F2,JF2,np.array([0,0]),0.0001,100)
print('x =',x2,'\n')
print(F2(x2))

x = [0.5884784  0.98231792] 

[-1.11022302e-16  7.53645872e-05]


Lorsque la fonction $f$ est à valeurs réelles, la routine `scipy.optimize.newton(f,x0,f')` implémente la méthode de Newton-Raphson pour une fonction $f$, sa dérivée $f'$, et un point d'initialisation $x_0$ :

In [4]:
# Test de la fonction scipy.optimize.newton pour la fonction F3(x)=x^2-2
def F3(x):
    return(x**2-2)
def F3prime(x):
    return(2*x)
x3=sc_opt.newton(F3,1.5,F3prime)
print('x =',x3,'\n')
print(x3-np.sqrt(2))

x = 1.4142135623730951 

0.0


Lorsque la fonction $f$ est à valeur vectorielle, il vaut mieux utiliser la routine `scipy.optimize.root(f,x0)` qui cherche un zéro de cette fonction par une méthode hybride, analogue multi-dimensionel des méthodes de la sécante et de la dichotomie que nous allons désormais décrire. Cette routine est plus robuste, et permet de traiter tous les exemples précédents :

In [5]:
# Test de la fonction scipy.optimize.root pour déterminer la solution (x,y) des équations cos(x)-sin(y)=exp(−x)-cos(y)=0
print(sc_opt.root(F2,np.array([0,0])),'\n')
# Test de la fonction scipy.optimize.root pour déterminer un zéro x de la fonction F3(x)=x^2-2
print(sc_opt.root(F3,1.5),'\n')

 message: The solution converged.
 success: True
  status: 1
     fun: [-1.099e-13  1.583e-13]
       x: [ 5.885e-01  9.823e-01]
    nfev: 13
    fjac: [[ 7.325e-01  6.808e-01]
           [-6.808e-01  7.325e-01]]
       r: [-7.805e-01  1.596e-01  9.871e-01]
     qtf: [ 4.439e-11  3.099e-10] 

 message: The solution converged.
 success: True
  status: 1
     fun: [ 4.441e-16]
       x: [ 1.414e+00]
    nfev: 7
    fjac: [[-1.000e+00]]
       r: [-2.828e+00]
     qtf: [-4.511e-12] 



## III. Méthode de la sécante

Considérons une fonction $F$ définie sur $\mathbb{R}$ et à valeurs réelles. Étant donnés deux réels distincts $x_0$ et $x_1$, nous approchons cette fonction par la fonction affine
$$
F_\text{app}(x) = F(x_0) + \frac{x - x_0}{x_1 - x_0} \big( F(x_1) - F(x_0) \big),
$$
lorsque cette fonction approchée est bien définie. Cette fonction affine s'annule en
$$
x_2 = \frac{x_0 F(x_1) - x_1 F(x_0)}{F(x_1) - F(x_0)},
$$
nombre qui donne une valeur approchée d'une racine de la fonction $F$. Nous pouvons améliorer cette valeur en itérant cet algorithme, pour les réels $x_1$ et $x_2$, puis $x_2$ et $x_3$, et ainsi de suite.

La suite $(x_n)_{n \geq 0}$ ainsi définie peut ne pas converger. Comme pour la méthode de Newton-Raphson, nous introduisons un seuil d'erreur $\varepsilon > 0$ et un nombre d'itérations maximal $N \geq 1$, et arrêtons l'algorithme soit lorsque $|F(x_n)| < \varepsilon$ auquel cas il renvoie la valeur approchée $x_n$, soit lorsque le nombre d'itérations a dépassé $N$, auquel cas il renvoie le message "L'algorithme n'a pas convergé" :

In [6]:
def secante(F,x0,x1,eps,N):
    x=x0
    y=x1
    z=0
    n=0
    e=2*eps
    while e>eps and n<N:
        z=x-(y-x)*F(x)/(F(y)-F(x))
        x=y
        y=z
        n=n+1
        e=abs(F(y))
    if n<N:
        return(y)
    else:
        return("L'algorithme n'a pas convergé.")
# Test de la fonction secante pour la fonction F3
z3=secante(F3,1,2,0.000000001,100)
print('x =',z3,'\n')
print(z3-np.sqrt(2))

x = 1.4142135620573204 

-3.157747396898003e-10


La routine `scipy.optimize.newton(f,x0)` implémente la méthode de la sécante pour une fonction $f$ et une estimation d'un de ses zéros $x_0$ :

In [7]:
t3=sc_opt.newton(F3,1)
print('x =',t3,'\n')
print(t3-np.sqrt(2))

x = 1.414213562373095 

-2.220446049250313e-16


## IV. Méthode de la dichotomie

Supposons que $F$ est une fonction continue sur $[x_0, y_0]$ qui prend des valeurs de signes opposés aux extrémités de l'intervalle
$$
F(x_0) F(y_0) \leq 0.
$$
Par le théorème des valeurs intermédiaires, la fonction $F$ admet un zéro dans $[x_0, y_0]$. La méthode de la dichotomie consiste à poser
$$
z_0 = \frac{x_0+y_0}{2},$$
et a étudié le signe de $F(z_0)$. Si ce signe est identique à celui de $F(x_0)$, alors nous posons $x_1 = z_0$ et $y_1 = y_0$. Sinon, nous posons $x_1 = x_0$ et $y_1 = z_0$. Dans les deux cas, nous avons
$$
F(x_1) F(y_1)\leq 0,
$$
et nous pouvons itérer l'algorithme. Étant donné un seuil d'erreur $\varepsilon > 0$, nous pouvons décider de l'arrêter lorsque $|F(z_k)| < \varepsilon$ et de renvoyer la valeur approchée d'un zéro donnée par $z_k$ :

In [8]:
def dichotomie(F,a0,b0,eps):
    a=a0
    b=b0
    c=0
    e=2*eps
    while e>eps:
        c=(a+b)/2
        if F(c)*F(a)>=0:
            a=c
        else:
            b=c
        e=abs(F(c))
    return(c)
# Test de la fonction dichotomie pour la fonction F4(x)=sin(x)-1/2
def F4(x):
    return np.sin(x)-1/2
x4=dichotomie(F4,-1.5,1.5,0.0000001)
print('x =',x4,'\n')
print(np.sin(x4))

x = 0.5235986709594727 

0.4999999093801155


La routine `scipy.optimize.bisect(f,a,b)` implémente la méthode de la dichotomie pour une fonction $f$, et deux points initiaux $a$ et $b$ :

In [9]:
z4=sc_opt.bisect(F4,-1.5,1.5)
print('x =',z4,'\n')
print(np.sin(z4))

x = 0.5235987755982023 

0.4999999999999164


## Exercices

### Exercice 1.

Nous introduisons la méthode de la fausse position pour résoudre l'équation $F(x) = 0$. Si $F$ est une fonction continue sur $\mathbb{R}$, et $x_0 < y_0$ sont deux nombres tels que $F(x_0) < 0 < F(y_0)$, alors $F$ admet un zéro dans l'intervalle $]x_0, y_0[$. Nous pouvons approcher la fonction $F$ sur cet intervalle par la fonction affine
$$
F_\text{app}(x) = F(x_0) + \frac{x - x_0}{y_0 - x_0} \big( F(y_0) - F(x_0) \big),
$$
qui s'annule en
$$
z_0 = \frac{x_0 F(y_0) - F(x_0) y_0}{F(y_0) - F(x_0)} \in ]x_0, y_0[.
$$
Dans le cas où $F(z_0) > 0$, la fonction $F$ admet un zéro dans $]x_0, z_0[$, et nous posons $x_1 = x_0$ et $y_1 = z_0$. Dans le cas où $F(z_0) < 0$, elle a un zéro dans $]z_0, y_0[$, et nous posons $x_1 = z_0$ et $y_1 = y_0$. Nous pouvons alors itérer cet algorithme pour obtenir une meilleure valeur approchée du zéro de $F$. Étant donné un seuil d'erreur $\varepsilon > 0$, nous pouvons arrêter la construction des suites $(x_n)_{n \geq 0}$ et $(y_n)_{n \geq 0}$ lorsque $|F(x_n)| < \varepsilon$ ou $|F(y_n)| < \varepsilon$, et renvoyer les valeurs de $x_n$ ou $y_n$.

1. Écrire une fonction `fausse-pos(F,x0,y0,epsilon)` qui prend en entrée une fonction $F$, deux réels $x_0 < y_0$ et un seuil d'erreur $\varepsilon > 0$, et renvoie le résultat de la méthode de la fausse position.

2. Tester la fonction `fauss-pos` pour les fonctions
$$
\forall x \in \mathbb{R}, \, G_1(x) = e^x - 2, \quad \text{ et } \quad G_2(x) = x^3 - 3 x + 2.
$$

### Exercice 2.

1. Déterminer numériquement un zéro $(x^*,y^*,z^*)$ de la fonction
$$
F(x, y, z) = \Big( - x - 7 y + z + x y - 1, 2 x + 4 y + 2 z + y z - \frac{1}{2}, 2 x + 6 y + x z^2 + 1 \Big),
$$
par :
- la méthode de Newton-Raphson implémentée par la fonction `Newton_Raphson` précédente,
- la routine `sc_opt.root` sans préciser la différentielle,
- la routine `sc_opt.root` en précisant la différentielle.

2. Choisir un vecteur $(x_0,y_0,z_0)$ proche, mais différent de $(x^*,y^*,z^*)$, et essayer de résoudre ce système en appliquant la fonction `Banach` à la fonction
$$
G(x, y, z) = F(x, y, z) + (x, y, z),
$$
pour le point initial $(x_0,y_0,z_0)$. L'algorithme converge-t-il ?

3.a. Calculer numériquement le rayon spectral de la différentielle de la fonction $G$ au point $(x^*,y^*,z^*)$.

b. Proposer une explication théorique à la réponse à la question 2.

### Exercice 3.

Nous cherchons à implémenter une nouvelle méthode exacte pour déterminer les décimales d'une solution d'une équation polynomiale à coefficient entiers, sans se limiter à la précision des flottants, ni utiliser des bibliothèques spécifiques pour améliorer la précision des calculs, mais simplement le fait de manipuler les entiers de manière exacte. Plus précisément, nous cherchons à résoudre
$$
P_0(x) = 0,
$$
où $P_0(x) = a_0 + a_1 x + \ldots + a_n x^n$ est un polynôme à coefficients entiers relatifs.

Nous supposons connaître un entier $u_0 \in \mathbb{Z}$ tel que $P_0(u_0) \leq 0$ et $P_0(u_0 + 1) > 0$, de sorte que $P_0$ admet une racine $x^*$ dans l'intervalle $[u_0, u_0 + 1)$, et nous remarquons que
$$
P_0(x^*) = 0 \Leftrightarrow 10^n a_0 + 10^{n-1} a_1 (10 x^*) + \ldots + 10 a_{n-1} (10 x^*)^{n-1} + a_n (10 x^*)^n = 0,
$$
c'est-à-dire que $10 \, x^*$ est une racine du polynôme
$$
P_1(x)=10^na_0+10^{n-1}a_1 x+...+10 a_{n-1}x^{n-1}+a_nx^n.
$$
Le polynôme $P_1$ admet donc une racine dans l'intervalle $[10 \, u_0, 10 \, u_0 + 10)$. De plus, nous pouvons déterminer un entier $0 \leq k_1 \leq 9$ tel que $P_1(10 \, u_0 + k_1) \leq 0$ et $P_1(10 u_0 + k_1 + 1) > 0$. Nous pouvons alors définir l'entier
$$
u_1 = 10 u_0 + k_1,
$$
et itérer l'agorithme précédent pour le polynôme $P_1$. Nous construisons ainsi une suite de polynômes $(P_i)_{i \geq 0}$ et d'entiers relatifs $(u_i)_{i \geq 0}$.

1. Vérifier que la suite $10^{- i} u_i$ admet une limite $x^*$ lorsque $i \to + \infty$ qui est une racine du polynôme $P_0$.

2. Coder cet algorithme pour déterminer les $100$ premières décimales de racine de deux.